In [1]:
import math
import random

import gym
import numpy as np

import torch
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
from torch.distributions import Normal

In [2]:
from IPython.display import clear_output
import matplotlib.pyplot as plt
%matplotlib inline

In [3]:
seed_number = 999

<h2>Use CUDA</h2>

In [4]:
np.random.seed(seed_number)
torch.backends.cudnn.deterministic = True
torch.manual_seed(seed_number)

use_cuda = torch.cuda.is_available()

if use_cuda:
    torch.cuda.manual_seed_all(seed_number)
    device = torch.device("cuda")
else:
    device = torch.device("cpu")

<h2>Create Environments</h2>

In [5]:
class BitFlip():
    def __init__(self, n, reward_type, max_steps):
        self.number_of_bits = n # number of bits
        self.reward_type = reward_type
        self.max_steps = max_steps
    def reset(self):
        self.n_steps = 0
        self.goal = np.random.randint(2, size=(self.number_of_bits)) # a random sequence of 0's and 1's
        self.state = np.random.randint(2, size=(self.number_of_bits)) 
        return np.array(self.state) ,np.array(self.goal)
    def step(self, action):
        if action >= self.number_of_bits:
            raise Exception('Action out of range')
        self.n_steps += 1
        self.state[action] = 1-self.state[action] # flip this bit
        done = np.array_equal(self.state, self.goal) or (self.max_steps <= self.n_steps)
        if self.reward_type == 'sparse':
            reward = 0 if np.array_equal(self.state, self.goal) else -1
        else:
            reward = -np.sum(np.square(self.state-self.goal))
        return np.array(self.state), reward, done, {}
    def render(self):
        print("\rstate :", np.array_str(self.state), ", goal :", np.array_str(self.goal), end=' '*10)
    def get_state_dim(self):
        state_dim = self.number_of_bits
        return state_dim
    def get_action_dim(self):
        action_dim = self.number_of_bits # since it is determining which bit to change
        return action_dim
    
BITS_NUMBER = 8
MAX_STEPS = BITS_NUMBER
env = BitFlip(BITS_NUMBER, 'sparse', MAX_STEPS)

<h2>Neural Network</h2>

In [6]:
def init_weights(m):
    if isinstance(m, nn.Linear):
        nn.init.normal_(m.weight, mean=0., std=0.1)
        nn.init.constant_(m.bias, 0.1)
        

class ActorCritic(nn.Module):
    def __init__(self, num_inputs, num_outputs, hidden_size, std=0.0):
        super(ActorCritic, self).__init__()
        
        self.critic = nn.Sequential(
            nn.Linear(num_inputs, hidden_size),
            nn.ReLU(),
            nn.Linear(hidden_size, 1)
        )
        
        self.actor = nn.Sequential(
            nn.Linear(num_inputs, hidden_size),
            nn.ReLU(),
            nn.Linear(hidden_size, num_outputs),
        )
        self.apply(init_weights)
        
    def forward(self, x):
        value = self.critic(x)
        act   = nn.functional.log_softmax(self.actor(x))
        return act, value

In [7]:
def plot(frame_idx, rewards):
    clear_output(True)
    plt.figure(figsize=(20,5))
    plt.subplot(131)
    plt.title('frame %s. reward: %s' % (frame_idx, rewards[-1]))
    plt.plot(rewards)
    plt.show()
    
def test_env(model, vis=False):
#     print ('\nevaluate performance')
    state = env.reset()
    state = state[0]
    done = False
    total_reward = 0
    while not done :
        if vis: 
            env.render()
        state = torch.FloatTensor(state).unsqueeze(0).to(device)
        act, _ = model(state)
        next_state, reward, done, _ = env.step(np.argmax(torch.exp(act).data.cpu().numpy()[0]))
        state = next_state
        total_reward += reward
#     print ('\ntotal_reward: ', total_reward)
    return total_reward

<h2>GAE</h2>

In [8]:
def compute_gae(next_value, rewards, masks, values, gamma=0.99, tau=0.95):
    values = values + [next_value]
    gae = 0
    returns = []
    for step in reversed(range(len(rewards))):
        delta = rewards[step] + gamma * values[step + 1].cuda() * masks[step] - values[step].cuda()
        gae = delta + gamma * tau * masks[step] * gae
        returns.insert(0, gae + values[step].cuda())
    return returns

<h1> Proximal Policy Optimization Algorithm</h1>
<h2><a href="https://arxiv.org/abs/1707.06347">Arxiv</a></h2>

In [9]:
def ppo_iter(mini_batch_size, states, actions, log_probs, returns, advantage):
    batch_size = states.size(0)
    actions = np.array(actions).reshape(len(actions), 1)
    log_probs = np.array(log_probs).reshape(len(log_probs),1)
    returns = returns.view(len(returns),-1)
    advantage = advantage.view(len(advantage),-1)
    for _ in range(batch_size // mini_batch_size):
        rand_ids = np.random.randint(0, batch_size, mini_batch_size)
        yield states[rand_ids, :], actions[rand_ids, :], log_probs[rand_ids, :], returns[rand_ids, :], advantage[rand_ids, :]
        
def ppo_update(ppo_epochs, mini_batch_size, states, actions, old_log_probs, returns, advantages, clip_param=0.2):
    print ('update ppo')
    actor_loss_list = []
    critic_loss_list = []
    
    for _ in range(ppo_epochs):
        for state, action, old_log_probs, return_, advantage in ppo_iter(mini_batch_size, states, actions, log_probs, returns, advantages):
            act, value = model(state)
            action = np.argmax((torch.exp(act).data.cpu().numpy()),axis = 1)
            one_hot_action = to_one_hot(action, BITS_NUMBER)
            new_log_probs = np.sum((torch.exp(act).data.cpu().numpy() * one_hot_action),1)
            ratio = np.exp(new_log_probs - old_log_probs)
            ratio = torch.FloatTensor(ratio).to(device)
            surr1 = ratio * advantage
            surr2 = torch.clamp(ratio, 1.0 - clip_param, 1.0 + clip_param) * advantage
            actor_loss  = - torch.min(surr1, surr2).mean()
            critic_loss = (returns - value).pow(2).mean()

            actor_loss_list.append(actor_loss.data.cpu().numpy().item(0))
            critic_loss_list.append(critic_loss.data.cpu().numpy().item(0))

            loss = 0.5 * critic_loss + actor_loss 

            optimizer.zero_grad()
            loss.backward()
            optimizer.step()
    mean_actor_loss = np.mean(actor_loss_list)
    mean_critic_loss = np.mean(critic_loss_list)
    
    mean_actor_loss_list.append(mean_actor_loss)
    mean_critic_loss_list.append(mean_critic_loss)

<h2>Training Agent </h2>

In [10]:
def to_one_hot(index, dim):
    if isinstance(index, np.int) or isinstance(index, np.int64):
        one_hot = np.zeros(dim)
        one_hot[index] = 1.
    else:
        one_hot = np.zeros((len(index), dim))
        one_hot[np.arange(len(index)), index] = 1.
    return one_hot

In [11]:
num_inputs  = env.get_state_dim()
num_outputs = env.get_action_dim()

#Hyper params:
hidden_size      = 256
lr               = 3e-4
num_restarts     = 16
mini_batch_size  = 16
ppo_epochs       = 4

model = ActorCritic(num_inputs, num_outputs, hidden_size).to(device)
optimizer = optim.Adam(model.parameters(), lr=lr)

ep_max     = 28000
ep_count   = 0
eval_num   = 1
num_steps  = 0

test_rewards = []
mean_actor_loss_list = []
mean_critic_loss_list = []

state = env.reset()
state = state[0]

zero_reward_count = 0
done = False
while ep_count < ep_max:

    log_probs = []
    values    = []
    states    = []
    actions   = []
    rewards   = []
    masks     = []
    entropy = 0

    for _ in range(num_restarts):
        done = False
        state = env.reset()
        state = state[0]
        while not done:
            state = torch.FloatTensor(state).to(device)
            act, value = model(state)
            action = np.argmax(act.data.cpu().numpy())
            one_hot_action = to_one_hot(action, BITS_NUMBER)
            log_prob = np.sum(act.data.cpu().numpy() * one_hot_action)
            next_state, reward, done, _ = env.step(action)
            if reward == 0:
                zero_reward_count += 1 
            log_probs.append(log_prob)
            values.append(value)
            rewards.append(reward)
            masks.append(1-done)

            state = list(state.data.cpu().numpy())
            states.append(state)
            actions.append(action)
            state = next_state
            num_steps += 1
#             print ('done: ', done)
    ep_count += 1
    
    if ep_count % eval_num == 0:
        test_reward = np.mean([test_env(model, False) for _ in range(10)])
        test_rewards.append(test_reward)

        print ('\nepisode {0} mean_rewards: {1}'.format(ep_count,test_reward))
        # plot(frame_idx, test_rewards)
            
    zero_freq = float(zero_reward_count) / num_steps
    other_freq = 1 - zero_freq 
    
    next_state = torch.FloatTensor(next_state).to(device)
    _, next_value = model(next_state)
    returns = compute_gae(next_value, rewards, masks, values)

#     print ('returns: ', returns)
    returns   = torch.cat(returns).detach()
    values    = torch.cat(values).detach()
    states    = torch.FloatTensor(states).to(device)
    advantage = returns - values
    
    ppo_update(ppo_epochs, mini_batch_size, states, actions, log_probs, returns, advantage)
    print ('====================================================================')
print ('zero_reward_count: ', zero_reward_count)
print ('zero_freq: ', zero_freq)

/home/weixiang/DML_MF_BO/env3/lib/python3.5/site-packages/ipykernel/__main__.py:26: UserWarning: Implicit dimension choice for log_softmax has been deprecated. Change the call to include dim=X as an argument.



episode 1 mean_rewards: -8.0
update ppo

episode 2 mean_rewards: -8.0
update ppo

episode 3 mean_rewards: -8.0
update ppo

episode 4 mean_rewards: -8.0
update ppo

episode 5 mean_rewards: -8.0
update ppo

episode 6 mean_rewards: -8.0
update ppo

episode 7 mean_rewards: -8.0
update ppo

episode 8 mean_rewards: -8.0
update ppo

episode 9 mean_rewards: -8.0
update ppo

episode 10 mean_rewards: -8.0
update ppo

episode 11 mean_rewards: -8.0
update ppo

episode 12 mean_rewards: -8.0
update ppo

episode 13 mean_rewards: -8.0
update ppo

episode 14 mean_rewards: -8.0
update ppo

episode 15 mean_rewards: -8.0
update ppo

episode 16 mean_rewards: -8.0
update ppo

episode 17 mean_rewards: -8.0
update ppo

episode 18 mean_rewards: -8.0
update ppo

episode 19 mean_rewards: -7.3
update ppo

episode 20 mean_rewards: -8.0
update ppo

episode 21 mean_rewards: -8.0
update ppo

episode 22 mean_rewards: -8.0
update ppo

episode 23 mean_rewards: -8.0
update ppo

episode 24 mean_rewards: -8.0
update ppo




episode 75 mean_rewards: -8.0
update ppo

episode 76 mean_rewards: -8.0
update ppo

episode 77 mean_rewards: -8.0
update ppo

episode 78 mean_rewards: -8.0
update ppo

episode 79 mean_rewards: -8.0
update ppo

episode 80 mean_rewards: -8.0
update ppo

episode 81 mean_rewards: -8.0
update ppo

episode 82 mean_rewards: -8.0
update ppo

episode 83 mean_rewards: -8.0
update ppo

episode 84 mean_rewards: -8.0
update ppo

episode 85 mean_rewards: -8.0
update ppo

episode 86 mean_rewards: -8.0
update ppo

episode 87 mean_rewards: -8.0
update ppo

episode 88 mean_rewards: -8.0
update ppo

episode 89 mean_rewards: -8.0
update ppo

episode 90 mean_rewards: -8.0
update ppo

episode 91 mean_rewards: -8.0
update ppo

episode 92 mean_rewards: -8.0
update ppo

episode 93 mean_rewards: -8.0
update ppo

episode 94 mean_rewards: -8.0
update ppo

episode 95 mean_rewards: -8.0
update ppo

episode 96 mean_rewards: -8.0
update ppo

episode 97 mean_rewards: -8.0
update ppo

episode 98 mean_rewards: -8.0
upd


episode 149 mean_rewards: -7.2
update ppo

episode 150 mean_rewards: -8.0
update ppo

episode 151 mean_rewards: -8.0
update ppo

episode 152 mean_rewards: -8.0
update ppo

episode 153 mean_rewards: -8.0
update ppo

episode 154 mean_rewards: -8.0
update ppo

episode 155 mean_rewards: -8.0
update ppo

episode 156 mean_rewards: -8.0
update ppo

episode 157 mean_rewards: -8.0
update ppo

episode 158 mean_rewards: -8.0
update ppo

episode 159 mean_rewards: -7.2
update ppo

episode 160 mean_rewards: -8.0
update ppo

episode 161 mean_rewards: -8.0
update ppo

episode 162 mean_rewards: -7.3
update ppo

episode 163 mean_rewards: -8.0
update ppo

episode 164 mean_rewards: -8.0
update ppo

episode 165 mean_rewards: -7.3
update ppo

episode 166 mean_rewards: -8.0
update ppo

episode 167 mean_rewards: -8.0
update ppo

episode 168 mean_rewards: -8.0
update ppo

episode 169 mean_rewards: -8.0
update ppo

episode 170 mean_rewards: -8.0
update ppo

episode 171 mean_rewards: -8.0
update ppo

episode 17


episode 222 mean_rewards: -8.0
update ppo

episode 223 mean_rewards: -8.0
update ppo

episode 224 mean_rewards: -8.0
update ppo

episode 225 mean_rewards: -8.0
update ppo

episode 226 mean_rewards: -8.0
update ppo

episode 227 mean_rewards: -8.0
update ppo

episode 228 mean_rewards: -8.0
update ppo

episode 229 mean_rewards: -8.0
update ppo

episode 230 mean_rewards: -8.0
update ppo

episode 231 mean_rewards: -7.3
update ppo

episode 232 mean_rewards: -8.0
update ppo

episode 233 mean_rewards: -8.0
update ppo

episode 234 mean_rewards: -8.0
update ppo

episode 235 mean_rewards: -8.0
update ppo

episode 236 mean_rewards: -8.0
update ppo

episode 237 mean_rewards: -8.0
update ppo

episode 238 mean_rewards: -8.0
update ppo

episode 239 mean_rewards: -8.0
update ppo

episode 240 mean_rewards: -8.0
update ppo

episode 241 mean_rewards: -8.0
update ppo

episode 242 mean_rewards: -8.0
update ppo

episode 243 mean_rewards: -8.0
update ppo

episode 244 mean_rewards: -8.0
update ppo

episode 24

...


episode 27673 mean_rewards: -8.0
update ppo

episode 27674 mean_rewards: -8.0
update ppo

episode 27675 mean_rewards: -8.0
update ppo

episode 27676 mean_rewards: -8.0
update ppo

episode 27677 mean_rewards: -8.0
update ppo

episode 27678 mean_rewards: -8.0
update ppo

episode 27679 mean_rewards: -8.0
update ppo

episode 27680 mean_rewards: -8.0
update ppo

episode 27681 mean_rewards: -8.0
update ppo

episode 27682 mean_rewards: -8.0
update ppo

episode 27683 mean_rewards: -8.0
update ppo

episode 27684 mean_rewards: -8.0
update ppo

episode 27685 mean_rewards: -8.0
update ppo

episode 27686 mean_rewards: -8.0
update ppo

episode 27687 mean_rewards: -8.0
update ppo

episode 27688 mean_rewards: -8.0
update ppo

episode 27689 mean_rewards: -8.0
update ppo

episode 27690 mean_rewards: -8.0
update ppo

episode 27691 mean_rewards: -8.0
update ppo

episode 27692 mean_rewards: -8.0
update ppo

episode 27693 mean_rewards: -8.0
update ppo

episode 27694 mean_rewards: -8.0
update ppo

episode 2


episode 27745 mean_rewards: -8.0
update ppo

episode 27746 mean_rewards: -8.0
update ppo

episode 27747 mean_rewards: -8.0
update ppo

episode 27748 mean_rewards: -8.0
update ppo

episode 27749 mean_rewards: -8.0
update ppo

episode 27750 mean_rewards: -8.0
update ppo

episode 27751 mean_rewards: -8.0
update ppo

episode 27752 mean_rewards: -8.0
update ppo

episode 27753 mean_rewards: -8.0
update ppo

episode 27754 mean_rewards: -8.0
update ppo

episode 27755 mean_rewards: -8.0
update ppo

episode 27756 mean_rewards: -8.0
update ppo

episode 27757 mean_rewards: -8.0
update ppo

episode 27758 mean_rewards: -8.0
update ppo

episode 27759 mean_rewards: -8.0
update ppo

episode 27760 mean_rewards: -8.0
update ppo

episode 27761 mean_rewards: -8.0
update ppo

episode 27762 mean_rewards: -8.0
update ppo

episode 27763 mean_rewards: -7.3
update ppo

episode 27764 mean_rewards: -8.0
update ppo

episode 27765 mean_rewards: -8.0
update ppo

episode 27766 mean_rewards: -8.0
update ppo

episode 2


episode 27818 mean_rewards: -8.0
update ppo

episode 27819 mean_rewards: -8.0
update ppo

episode 27820 mean_rewards: -8.0
update ppo

episode 27821 mean_rewards: -8.0
update ppo

episode 27822 mean_rewards: -8.0
update ppo

episode 27823 mean_rewards: -7.3
update ppo

episode 27824 mean_rewards: -8.0
update ppo

episode 27825 mean_rewards: -8.0
update ppo

episode 27826 mean_rewards: -8.0
update ppo

episode 27827 mean_rewards: -8.0
update ppo

episode 27828 mean_rewards: -8.0
update ppo

episode 27829 mean_rewards: -8.0
update ppo

episode 27830 mean_rewards: -8.0
update ppo

episode 27831 mean_rewards: -7.2
update ppo

episode 27832 mean_rewards: -8.0
update ppo

episode 27833 mean_rewards: -8.0
update ppo

episode 27834 mean_rewards: -8.0
update ppo

episode 27835 mean_rewards: -8.0
update ppo

episode 27836 mean_rewards: -8.0
update ppo

episode 27837 mean_rewards: -7.2
update ppo

episode 27838 mean_rewards: -8.0
update ppo

episode 27839 mean_rewards: -8.0
update ppo

episode 2


episode 27891 mean_rewards: -8.0
update ppo

episode 27892 mean_rewards: -8.0
update ppo

episode 27893 mean_rewards: -8.0
update ppo

episode 27894 mean_rewards: -8.0
update ppo

episode 27895 mean_rewards: -8.0
update ppo

episode 27896 mean_rewards: -7.3
update ppo

episode 27897 mean_rewards: -8.0
update ppo

episode 27898 mean_rewards: -8.0
update ppo

episode 27899 mean_rewards: -7.2
update ppo

episode 27900 mean_rewards: -8.0
update ppo

episode 27901 mean_rewards: -8.0
update ppo

episode 27902 mean_rewards: -8.0
update ppo

episode 27903 mean_rewards: -8.0
update ppo

episode 27904 mean_rewards: -7.3
update ppo

episode 27905 mean_rewards: -8.0
update ppo

episode 27906 mean_rewards: -8.0
update ppo

episode 27907 mean_rewards: -8.0
update ppo

episode 27908 mean_rewards: -8.0
update ppo

episode 27909 mean_rewards: -8.0
update ppo

episode 27910 mean_rewards: -7.2
update ppo

episode 27911 mean_rewards: -7.2
update ppo

episode 27912 mean_rewards: -8.0
update ppo

episode 2


episode 27964 mean_rewards: -8.0
update ppo

episode 27965 mean_rewards: -8.0
update ppo

episode 27966 mean_rewards: -8.0
update ppo

episode 27967 mean_rewards: -8.0
update ppo

episode 27968 mean_rewards: -8.0
update ppo

episode 27969 mean_rewards: -8.0
update ppo

episode 27970 mean_rewards: -8.0
update ppo

episode 27971 mean_rewards: -8.0
update ppo

episode 27972 mean_rewards: -8.0
update ppo

episode 27973 mean_rewards: -7.2
update ppo

episode 27974 mean_rewards: -7.3
update ppo

episode 27975 mean_rewards: -8.0
update ppo

episode 27976 mean_rewards: -7.6
update ppo

episode 27977 mean_rewards: -8.0
update ppo

episode 27978 mean_rewards: -8.0
update ppo

episode 27979 mean_rewards: -8.0
update ppo

episode 27980 mean_rewards: -8.0
update ppo

episode 27981 mean_rewards: -8.0
update ppo

episode 27982 mean_rewards: -8.0
update ppo

episode 27983 mean_rewards: -8.0
update ppo

episode 27984 mean_rewards: -8.0
update ppo

episode 27985 mean_rewards: -8.0
update ppo

episode 2

In [19]:
import pickle

with open('./Test Reward Plot/test_rewards_ppo_bitflipping8', 'wb') as fp1:
    pickle.dump(test_rewards, fp1)
with open('./Loss Plot/mean_actor_loss_ppo_bitflipping8', 'wb') as fp2:
    pickle.dump(mean_actor_loss_list, fp2)
with open('./Loss Plot/mean_critic_loss_ppo_bitflipping8', 'wb') as fp3:
    pickle.dump(mean_critic_loss_list, fp3)

<h1> Save and Load Model </h1>

In [13]:
torch.save(model, './Model/ppo_bitflipping8' )

/home/weixiang/DML_MF_BO/env3/lib/python3.5/site-packages/torch/serialization.py:241: UserWarning: Couldn't retrieve source code for container of type ActorCritic. It won't be checked for correctness upon loading.
  "type " + obj.__name__ + ". It won't be checked "


In [14]:
# expert_model = torch.load('./Model/ppo_bitflipping8')

In [15]:
# testing_number = 1
# expert_test_rewards = []
# for i in range(testing_number): 
#     expert_test_reward = test_env(expert_model)
#     expert_test_rewards.append(expert_test_reward)
#     print ('test {0}, total_reward from 15240 steps load model: {1}'.format(i+1, expert_test_reward))

# print ('mean expert test reward: ', np.mean(expert_test_rewards))

<h1>Saving trajectories</h1>

In [16]:
done = False
counter = 0
while not done:
    counter += 1
    print (done)
    if counter == 8:
        done = True

False
False
False
False
False
False
False
False
